In [4]:
# importing the libraries
import pandas as pd
import geopandas as gpd
import numpy as np
import math
import folium
from folium import Choropleth, Circle, Marker
from folium.plugins import HeatMap, MarkerCluster

In [5]:
# Create a map
m_1 = folium.Map(location=[42.32,-71.0589],tiles = 'openstreetmap', zoom_start=10)
# Display the map
m_1

In [6]:
# load the data
crimes = pd.read_csv("../input/geospatial-learn-course-data/crimes-in-boston/crimes-in-boston/crime.csv", encoding = 'latin-1')
crimes.head()

INCIDENT_NUMBER  OFFENSE_CODE    OFFENSE_CODE_GROUP   OFFENSE_DESCRIPTION  \
0      I182070945           619               Larceny    LARCENY ALL OTHERS   
1      I182070943          1402             Vandalism             VANDALISM   
2      I182070941          3410                 Towed   TOWED MOTOR VEHICLE   
3      I182070940          3114  Investigate Property  INVESTIGATE PROPERTY   
4      I182070938          3114  Investigate Property  INVESTIGATE PROPERTY   

  DISTRICT REPORTING_AREA SHOOTING     OCCURRED_ON_DATE  YEAR  MONTH  \
0      D14            808      NaN  2018-09-02 13:00:00  2018      9   
1      C11            347      NaN  2018-08-21 00:00:00  2018      8   
2       D4            151      NaN  2018-09-03 19:27:00  2018      9   
3       D4            272      NaN  2018-09-03 21:16:00  2018      9   
4       B3            421      NaN  2018-09-03 21:05:00  2018      9   

  DAY_OF_WEEK  HOUR    UCR_PART       STREET        Lat       Long  \
0      Sunday    13    Part One   LINCOLN ST  42.357791 -71.139371   
1     Tuesday     0    Part Two     HECLA ST  42.306821 -71.060300   
2      Monday    19  Part Three  CAZENOVE ST  42.346589 -71.072429   
3      Monday    21  Part Three   NEWCOMB ST  42.334182 -71.078664   
4      Monday    21  Part Three     DELHI ST  42.275365 -71.090361   

                      Location  
0  (42.35779134, -71.13937053)  
1  (42.30682138, -71.06030035)  
2  (42.34658879, -71.07242943)  
3  (42.33418175, -71.07866441)  
4  (42.27536542, -71.09036101)

In [7]:
# missing values in the dataset
missing_values = crimes.isnull().sum()
missing_values

INCIDENT_NUMBER             0
OFFENSE_CODE                0
OFFENSE_CODE_GROUP          0
OFFENSE_DESCRIPTION         0
DISTRICT                 1765
REPORTING_AREA              0
SHOOTING               318054
OCCURRED_ON_DATE            0
YEAR                        0
MONTH                       0
DAY_OF_WEEK                 0
HOUR                        0
UCR_PART                   90
STREET                  10871
Lat                     19999
Long                    19999
Location                    0
dtype: int64

In [8]:
missing_values[missing_values > 0]

DISTRICT      1765
SHOOTING    318054
UCR_PART        90
STREET       10871
Lat          19999
Long         19999
dtype: int64

In [9]:
# total missing values in numbers
total_missing_values = missing_values.sum()
total_missing_values

370778

In [10]:
crimes.shape

(319073, 17)

In [11]:
# total values in the dataset
total_values = np.product(crimes.shape)
total_values

5424241

In [12]:
#percent of missing values
percent = (total_missing_values / total_values) * 100
percent

6.83557386185459

In [17]:
crimes.OFFENSE_CODE_GROUP.unique()

array(['Larceny', 'Auto Theft', 'Robbery', 'Larceny From Motor Vehicle',
       'Residential Burglary', 'Simple Assault', 'Harassment'],
      dtype=object)

In [22]:
# Drop rows with missing locations
crimes.dropna(subset = ['Lat','Long','DISTRICT'], inplace = True)

# Focus on major crimes in 2018
crimes = crimes[crimes.OFFENSE_CODE_GROUP.isin([
    'Larceny','Auto Theft','Robbery','Larceny From Motor Vehicle', 'Residential Burglary',
    'Simple Assault','Harassment','Ballistics', 'Aggravated Assault', 'Other Burglary', 
    'Arson', 'Commercial Burglary', 'HOME INVASION', 'Homicide', 'Criminal Harassment', 
    'Manslaughter'
])]
# crimes = crimes[crimes.Year>=2018]
crimes.head()

INCIDENT_NUMBER  OFFENSE_CODE          OFFENSE_CODE_GROUP  \
0       I182070945           619                     Larceny   
6       I182070933           724                  Auto Theft   
8       I182070931           301                     Robbery   
19      I182070915           614  Larceny From Motor Vehicle   
24      I182070908           522        Residential Burglary   

                      OFFENSE_DESCRIPTION DISTRICT REPORTING_AREA SHOOTING  \
0                      LARCENY ALL OTHERS      D14            808      NaN   
6                              AUTO THEFT       B2            330      NaN   
8                        ROBBERY - STREET       C6            177      NaN   
19  LARCENY THEFT FROM MV - NON-ACCESSORY       B2            181      NaN   
24      BURGLARY - RESIDENTIAL - NO FORCE       B2            911      NaN   

       OCCURRED_ON_DATE  YEAR  MONTH DAY_OF_WEEK  HOUR  UCR_PART  \
0   2018-09-02 13:00:00  2018      9      Sunday    13  Part One   
6   2018-09-03 21:25:00  2018      9      Monday    21  Part One   
8   2018-09-03 20:48:00  2018      9      Monday    20  Part One   
19  2018-09-02 18:00:00  2018      9      Sunday    18  Part One   
24  2018-09-03 18:38:00  2018      9      Monday    18  Part One   

               STREET        Lat       Long                     Location  
0          LINCOLN ST  42.357791 -71.139371  (42.35779134, -71.13937053)  
6         NORMANDY ST  42.306072 -71.082733  (42.30607218, -71.08273260)  
8   MASSACHUSETTS AVE  42.331521 -71.070853  (42.33152148, -71.07085307)  
19         SHIRLEY ST  42.325695 -71.068168  (42.32569490, -71.06816778)  
24    ANNUNCIATION RD  42.335062 -71.093168  (42.33506218, -71.09316781)

In [23]:
daytime_robberies = crimes[((crimes.OFFENSE_CODE_GROUP == 'Robbery') & 
                           (crimes.HOUR.isin(range(9,18))))]

In [25]:
daytime_robberies.head()

INCIDENT_NUMBER  OFFENSE_CODE OFFENSE_CODE_GROUP    OFFENSE_DESCRIPTION  \
299       I182070598           311            Robbery   ROBBERY - COMMERCIAL   
527       I182070342           381            Robbery  ROBBERY - CAR JACKING   
562       I182070309           361            Robbery        ROBBERY - OTHER   
1127      I182069693           301            Robbery       ROBBERY - STREET   
1135      I182069687           301            Robbery       ROBBERY - STREET   

     DISTRICT REPORTING_AREA SHOOTING     OCCURRED_ON_DATE  YEAR  MONTH  \
299       A15             60      NaN  2018-09-02 17:15:00  2018      9   
527       E18            490      NaN  2018-09-01 17:05:00  2018      9   
562        D4            151      NaN  2018-09-01 15:00:00  2018      9   
1127       A1             74      NaN  2018-08-30 15:24:00  2018      8   
1135       B2            278      NaN  2018-08-28 12:00:00  2018      8   

     DAY_OF_WEEK  HOUR  UCR_PART          STREET        Lat       Long  \
299       Sunday    17  Part One  RUTHERFORD AVE  42.371673 -71.063264   
527     Saturday    17  Part One     CUMMINS HWY  42.276453 -71.112980   
562     Saturday    15  Part One     BERKELEY ST  42.346055 -71.070507   
1127    Thursday    15  Part One     BULFINCH PL  42.362191 -71.062238   
1135     Tuesday    12  Part One    HARRISON AVE  42.331538 -71.080157   

                         Location  
299   (42.37167264, -71.06326413)  
527   (42.27645319, -71.11297971)  
562   (42.34605510, -71.07050669)  
1127  (42.36219081, -71.06223802)  
1135  (42.33153805, -71.08015661)

In [36]:
# create a map
m_2 = folium.Map(location = [42.32,-71.0589], tiles='cartodbpositron', zoom_start = 15)

# Add points to the map
for idx, row in daytime_robberies.iterrows():
    Marker([row['Lat'], row['Long']]).add_to(m_2)

# Display Map
m_2

In [37]:
# create the map
m_3 = folium.Map(location=[42.32, -71.0589], tiles = 'cartodbpositron', zoom_start =13)

# Add points to the map
mc = MarkerCluster()
for idx, row in daytime_robberies.iterrows():
    if not math.isnan(row['Long']) and not math.isnan(row['Lat']):
        mc.add_child(Marker([row['Lat'], row['Long']]))
m_3.add_child(mc)

# Display the map
m_3


In [38]:
# Create a base map
m_4 = folium.Map(location=[42.32,-71.0589], tiles='cartodbpositron', zoom_start=13)

def color_producer(val):
    if val <= 12:
        return 'forestgreen'
    else:
        return 'darkred'

# Add a bubble map to the base map
for i in range(0,len(daytime_robberies)):
    Circle(
        location=[daytime_robberies.iloc[i]['Lat'], daytime_robberies.iloc[i]['Long']],
        radius=20,
        color=color_producer(daytime_robberies.iloc[i]['HOUR'])).add_to(m_4)

# Display the map
m_4

In [39]:
# Create a base map
m_5 = folium.Map(location=[42.32,-71.0589], tiles='cartodbpositron', zoom_start=12)

# Add a heatmap to the base map
HeatMap(data=crimes[['Lat', 'Long']], radius=10).add_to(m_5)

# Display the map
m_5

In [40]:
# GeoDataFrame with geographical boundaries of Boston police districts
districts_full = gpd.read_file('../input/geospatial-learn-course-data/Police_Districts/Police_Districts/Police_Districts.shp')
districts = districts_full[["DISTRICT", "geometry"]].set_index("DISTRICT")
districts.head()

geometry
DISTRICT                                                   
A15       MULTIPOLYGON (((-71.07416 42.39051, -71.07415 ...
A7        MULTIPOLYGON (((-70.99644 42.39557, -70.99644 ...
A1        POLYGON ((-71.05200 42.36884, -71.05169 42.368...
C6        POLYGON ((-71.04406 42.35403, -71.04412 42.353...
D4        POLYGON ((-71.07416 42.35724, -71.07359 42.357...

In [41]:
# Number of crimes in each police district
plot_dict = crimes.DISTRICT.value_counts()
plot_dict.head()

DISTRICT
D4     13155
B2      9657
A1      9171
C11     7812
B3      5880
Name: count, dtype: int64

In [42]:
# Create a base map
m_6 = folium.Map(location=[42.32,-71.0589], tiles='cartodbpositron', zoom_start=12)

# Add a choropleth map to the base map
Choropleth(geo_data=districts.__geo_interface__, 
           data=plot_dict, 
           key_on="feature.id", 
           fill_color='YlGnBu', 
           legend_name='Major criminal incidents (Jan-Aug 2018)'
          ).add_to(m_6)

# Display the map
m_6